In [0]:
%sh
wget http://download.geonames.org/export/dump/allCountries.zip -P /tmp

--2025-08-15 21:21:04--  http://download.geonames.org/export/dump/allCountries.zip
Resolving download.geonames.org (download.geonames.org)... 5.9.152.54
Connecting to download.geonames.org (download.geonames.org)|5.9.152.54|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 413952559 (395M) [application/zip]
Saving to: ‘/tmp/allCountries.zip’

     0K .......... .......... .......... .......... ..........  0%  259K 26m1s
    50K .......... .......... .......... .......... ..........  0%  522K 19m28s
   100K .......... .......... .......... .......... ..........  0% 12.7M 13m9s
   150K .......... .......... .......... .......... ..........  0% 48.0M 9m54s
   200K .......... .......... .......... .......... ..........  0%  541K 10m24s
   250K .......... .......... .......... .......... ..........  0% 20.6M 8m43s
   300K .......... .......... .......... .......... ..........  0% 44.0M 7m30s
   350K .......... .......... .......... .......... ..........  0% 66.1M 6m34

In [0]:
%sh
unzip /tmp/allCountries.zip -d /tmp

Archive:  /tmp/allCountries.zip
  inflating: /tmp/allCountries.txt   


In [0]:
%sh
mkdir -p /dbfs/FileStore/tables/
cp /tmp/allCountries.txt /dbfs/FileStore/tables/allCountries.txt

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql.types import StructType, StructField, StringType, DoubleType, IntegerType, LongType

# Initialize SparkSession
spark = SparkSession.builder \
    .appName("ReadGeonamesUSTabSeparatedFile") \
    .master("local[*]") \
    .getOrCreate()



# Official GeoNames schema (as of their documentation)
# The file is tab-delimited and has 19 columns.
# It's always best to define a schema for performance and correctness.
schema = StructType([
    StructField("geonameid", IntegerType(), True),
    StructField("name", StringType(), True),
    StructField("asciiname", StringType(), True),
    StructField("alternatenames", StringType(), True),
    StructField("latitude", DoubleType(), True),
    StructField("longitude", DoubleType(), True),
    StructField("feature_class", StringType(), True),
    StructField("feature_code", StringType(), True),
    StructField("country_code", StringType(), True),
    StructField("cc2", StringType(), True),
    StructField("admin1_code", StringType(), True),
    StructField("admin2_code", StringType(), True),
    StructField("admin3_code", StringType(), True),
    StructField("admin4_code", StringType(), True),
    StructField("population", LongType(), True),
    StructField("elevation", StringType(), True), # Elevation can be -9999, so reading as String or Integer with a custom parser is safer.
    StructField("dem", IntegerType(), True),
    StructField("timezone", StringType(), True),
    StructField("modification_date", StringType(), True) # Using StringType is safer as DateType requires a specific format string.
])
df = spark.read.csv(
    "dbfs:/FileStore/tables/allCountries.txt",
    sep="\t",
    header=False,
    schema = schema
)

In [0]:
df.show(5)

+---------+--------------------+--------------------+--------------------+--------+---------+-------------+------------+------------+-----+-----------+-----------+-----------+-----------+----------+---------+----+--------------+-----------------+
|geonameid|                name|           asciiname|      alternatenames|latitude|longitude|feature_class|feature_code|country_code|  cc2|admin1_code|admin2_code|admin3_code|admin4_code|population|elevation| dem|      timezone|modification_date|
+---------+--------------------+--------------------+--------------------+--------+---------+-------------+------------+------------+-----+-----------+-----------+-----------+-----------+----------+---------+----+--------------+-----------------+
|  2994701|           Roc Meler|           Roc Meler|Roc Mele,Roc Mele...|42.58765|   1.7418|            T|          PK|          AD|AD,FR|         02|       NULL|       NULL|       NULL|         0|     2811|2348|Europe/Andorra|       2023-10-03|
|  3017832|P

In [0]:
df.createOrReplaceTempView("hanfen")

In [0]:
%sql
Select * from hanfen;

geonameid name asciiname alternatenames latitude longitude feature_class feature_code country_code cc2 admin1_code admin2_code admin3_code admin4_code population elevation dem timezone modification_date 2994701 Roc Meler Roc Meler Roc Mele,Roc Meler,Roc Mélé 42.58765 1.7418 T PK AD AD,FR 02 null null null 0 2811 2348 Europe/Andorra 2023-10-03 3017832 Pic de les Abelletes Pic de les Abelletes Pic de la Font-Negre,Pic de la Font-Nègre,Pic de les Abelletes 42.52535 1.73343 T PK AD FR A9 66 663 66146 0 null 2411 Europe/Andorra 2014-11-05 3017833 Estany de les Abelletes Estany de les Abelletes Estany de les Abelletes,Etang de Font-Negre,Étang de Font-Nègre 42.52915 1.73362 H LK AD FR A9 null null null 0 null 2260 Europe/Andorra 2014-11-05 3023203 Port Vieux de la Coume d’Ose Port Vieux de la Coume d'Ose Port Vieux de Coume d'Ose,Port Vieux de Coume d’Ose,Port Vieux de la Coume d'Ose,Port Vieux de la Coume d’Ose 42.62568 1.61823 T PASS AD null 00 null null null 0 null 2687 Europe/Andorra 2014-11-05 3029315 Port de la Cabanette Port de la Cabanette Port de la Cabanette,Porteille de la Cabanette 42.6 1.73333 T PASS AD AD,FR B3 09 091 09139 0 null 2379 Europe/Andorra 2014-11-05 3034945 Roc de Port Dret Roc de Port Dret null 42.60288 1.45736 T PK AD AD,FR 04 null null null 0 2735 2650 Europe/Andorra 2023-12-24 3038814 Costa de Xurius Costa de Xurius null 42.50692 1.47569 T SLP AD null 07 null null null 0 null 1839 Europe/Andorra 2015-03-08 3038815 Font de la Xona Font de la Xona null 42.55003 1.44986 H SPNG AD null 04 null null null 0 null 1976 Europe/Andorra 2010-01-11 3038816 Xixerella Xixerella null 42.55327 1.48736 P PPL AD null 04 null null null 0 null 1417 Europe/Andorra 2009-04-24 3038818 Riu Xic Riu Xic null 42.57165 1.67554 H STM AD null 02 null null null 0 null 1851 Europe/Andorra 2014-12-03 3038819 Pas del Xic Pas del Xic null 42.49766 1.57597 R TRL AD null 08 null null null 0 null 1669 Europe/Andorra 2015-05-06 3038820 Roc del Xeig Roc del Xeig null 42.56068 1.4898 T RK AD null 04 null null null 0 null 1643 Europe/Andorra 2015-05-06 3038821 Collada del Xeig Collada del Xeig null 42.57512 1.49009 T PK AD null 04 null null null 0 null 1857 Europe/Andorra 2014-11-05 3038822 Fonts Vives Fonts Vives null 42.49829 1.56428 H SPNG AD null 08 null null null 0 null 1540 Europe/Andorra 2015-05-06 3038823 Roc de Vista Roc de Vista null 42.49922 1.48118 T RK AD null 07 null null null 0 null 1564 Europe/Andorra 2015-03-08 3038824 Obaga de Vista Obaga de Vista null 42.47935 1.44621 T SLP AD null 06 null null null 0 null 1749 Europe/Andorra 2015-03-08 3038825 Coll de Vista Coll de Vista null 42.47611 1.60578 T GAP AD null 06 null null null 0 null 2335 Europe/Andorra 2015-04-08 3038826 Coll de Vista Coll de Vista Coll de Vista 42.47552 1.44173 T PASS AD AD,ES 00 null null null 0 null 1967 Europe/Andorra 2014-11-05 3038827 Visanseny Visanseny Visanceny,Visanseny 42.57488 1.61616 L LCTY AD null 02 null null null 0 null 1706 Europe/Andorra 2014-12-03 3038828 Roc de la Vinya Roc de la Vinya null 42.52776 1.56446 T RK AD null 03 null null null 0 null 1260 Europe/Andorra 2015-02-06 3038829 Canal de la Vinya Canal de la Vinya null 42.52232 1.52319 H STM AD null 04 null null null 0 null 1183 Europe/Andorra 2015-05-06 3038830 Bosc de Villar Bosc de Villar null 42.60135 1.5434 V FRST AD null 05 null null null 0 null 1860 Europe/Andorra 2014-12-03 3038831 Torrent de Vila Torrent de Vila null 42.53414 1.56678 H STM AD null 03 null null null 0 null 1337 Europe/Andorra 2015-02-06 3038832 Vila Vila Casas Vila,Vila 42.53176 1.56654 P PPL AD null 03 null null null 1418 null 1318 Europe/Andorra 2024-11-04 3038833 Basers de Vicenç Basers de Vicenc null 42.47669 1.4829 T CLF AD null 06 null null null 0 null 1019 Europe/Andorra 2015-03-08 3038834 Pla de Viàs Pla de Vias null 42.59001 1.65996 T UPLD AD null 02 null null null 0 null 2052 Europe/Andorra 2014-12-03 3038835 Vial del Cardaire Vial del Cardaire null 42.56372 1.50503 L LCTY AD null 04 null null null 0 n

Databricks visualization. Run in Databricks to view.

## Top 10 Most Populated Places 
#### Where country code is not Null

In [0]:
df.select("name", "country_code", "population") \
  .filter((df.population > 0) & (df.country_code.isNotNull())) \
  .orderBy(df.population.desc()) \
  .show(10, truncate=False)

+-----------------------------+------------+----------+
|name                         |country_code|population|
+-----------------------------+------------+----------+
|Commonwealth of Nations      |GB          |2400000000|
|Indian Subcontinent          |IN          |1700000000|
|People’s Republic of China   |CN          |1411778724|
|Republic of India            |IN          |1352617328|
|Contiguous United States     |US          |328571074 |
|United States                |US          |327167434 |
|Republic of Indonesia        |ID          |267663435 |
|Islamic Republic of Pakistan |PK          |212215030 |
|Federative Republic of Brazil|BR          |209469333 |
|Uttar Pradesh                |IN          |199812341 |
+-----------------------------+------------+----------+
only showing top 10 rows


## Countries with the Most Named Locations

In [0]:
df.groupBy("country_code") \
  .count() \
  .orderBy("count", ascending=False) \
  .show(10)

+------------+-------+
|country_code|  count|
+------------+-------+
|          US|2241278|
|          CN| 943051|
|          IN| 659874|
|          NO| 607998|
|          FI| 545791|
|          MX| 486492|
|          ID| 452042|
|          RU| 402715|
|          CA| 315654|
|          TH| 264772|
+------------+-------+
only showing top 10 rows


## Top 10 Most Populous Cities Only

#### Filter for feature_code == PPL -populated place

In [0]:
df.filter(df.feature_code == 'PPL') \
  .select("name", "country_code", "population") \
  .orderBy("population", ascending=False) \
  .show(10, truncate=False)

+----------------+------------+----------+
|name            |country_code|population|
+----------------+------------+----------+
|Ho Chi Minh City|VN          |14002598  |
|New York City   |US          |8804190   |
|Ahmedabad       |IN          |6357693   |
|Dalian          |CN          |4913879   |
|Jeddah          |SA          |4697000   |
|Surat           |IN          |4591246   |
|New Taipei City |TW          |4004367   |
|Zibo            |CN          |3129228   |
|Pune            |IN          |3124458   |
|Kanpur          |IN          |2823249   |
+----------------+------------+----------+
only showing top 10 rows


## Top Timezones by Population

#### This shows where people are concentrated by time zone

In [0]:
timezone_conc = df.groupBy("timezone") \
  .agg({"population": "sum"}) \
  .orderBy("sum(population)", ascending=False) \
  .show(10, truncate=False)

display(timezone_conc)

+-----------------+---------------+
|timezone         |sum(population)|
+-----------------+---------------+
|NULL             |19498296988    |
|Asia/Kolkata     |8838091648     |
|Australia/Perth  |3822834598     |
|Europe/London    |2924369260     |
|Asia/Shanghai    |2477797023     |
|Africa/Lubumbashi|1157840799     |
|America/New_York |1130548438     |
|Africa/Bangui    |1044004614     |
|Asia/Karachi     |950192119      |
|America/Chicago  |934542971      |
+-----------------+---------------+
only showing top 10 rows


In [0]:
display(timezone_conc)

In [0]:
df.selectExpr(
    "min(latitude) as min_lat", 
    "max(latitude) as max_lat", 
    "min(longitude) as min_lon", 
    "max(longitude) as max_lon"
).show()

+-------+-------+-------+-------+
|min_lat|max_lat|min_lon|max_lon|
+-------+-------+-------+-------+
|  -90.0|   90.0| -180.0|  180.0|
+-------+-------+-------+-------+

